# Dolly v2 SageMaker Inference

This is a sample code to deploy Dolly v2 on SageMaker.

In [ ]:
!pip install "sagemaker>=2.143.0" -U

In [3]:
import sagemaker, boto3, json
from sagemaker import get_execution_role
from sagemaker.pytorch.model import PyTorchModel
from sagemaker.huggingface import HuggingFace

role = get_execution_role()
region = boto3.Session().region_name
sess = sagemaker.Session()
bucket = sess.default_bucket()

sagemaker.__version__

'2.145.0'

## Package and Upload Model

In [9]:
!rm -rf scripts/model
%cd scripts
!tar -czvf ../package.tar.gz *
%cd -

/root/LLM/AutoModel/scripts
code/
code/requirements.txt
code/.ipynb_checkpoints/
code/.ipynb_checkpoints/run_clm-checkpoint.py
code/.ipynb_checkpoints/finetune-checkpoint.py
code/.ipynb_checkpoints/inference-checkpoint.py
code/.ipynb_checkpoints/requirements-checkpoint.txt
code/inference.py
code/utils/
code/utils/prompter.py
code/utils/.ipynb_checkpoints/
code/utils/.ipynb_checkpoints/prompter-checkpoint.py
code/utils/__pycache__/
code/utils/__pycache__/__init__.cpython-37.pyc
code/utils/__pycache__/prompter.cpython-37.pyc
code/utils/__init__.py
code/finetune.py
code/run_clm.py
code/templates/
code/templates/alpaca.json
code/templates/.ipynb_checkpoints/
code/templates/.ipynb_checkpoints/stable_lm-checkpoint.json
code/templates/.ipynb_checkpoints/dolly-v2-checkpoint.json
code/templates/.ipynb_checkpoints/alpaca_short-checkpoint.json
code/templates/.ipynb_checkpoints/alpaca-checkpoint.json
code/templates/dolly-v2.json
code/templates/alpaca_short.json
code/templates/stable_lm.json
/root/

In [10]:
model_path = sess.upload_data('package.tar.gz', bucket=bucket, key_prefix=f"Dolly-v2")
model_path

's3://sagemaker-us-west-2-867115166077/Dolly-v2/package.tar.gz'

## Deploy Model

In [17]:
from sagemaker.async_inference import AsyncInferenceConfig
from sagemaker.serializers import JSONSerializer

endpoint_name = "Dolly-v2"

huggingface_model = PyTorchModel(
    model_data=model_path,
    framework_version="1.13",
    py_version='py39',
    role=role,
    name=endpoint_name,
    env={
        "model_params": json.dumps({
            "base_model": "databricks/dolly-v2-3b",
            "peft": False,
            "load_8bit": True,
            "prompt_template": "alpaca",
        })
        
    }
)

# deploy model to SageMaker Inference
predictor = huggingface_model.deploy(
    initial_instance_count=1,
    instance_type='ml.g5.2xlarge',
    endpoint_name=endpoint_name,
    serializer=JSONSerializer(),
    async_inference_config=AsyncInferenceConfig()
)

-----------!

## Run Inference

In [18]:
from sagemaker.predictor import Predictor
from sagemaker.predictor_async import AsyncPredictor
from sagemaker.serializers import JSONSerializer
from sagemaker.deserializers import NumpyDeserializer

predictor_client = AsyncPredictor(
    predictor=Predictor(
        endpoint_name=endpoint_name,
        sagemaker_session=sess,
        serializer=JSONSerializer(),
        deserializer=NumpyDeserializer()
    ),
    name=endpoint_name
)
data = {
    "instruction": "When was George Washington president?",
    "input": """George Washington (February 22, 1732[b] – December 14, 1799) was an American military officer, statesman,
and Founding Father who served as the first president of the United States from 1789 to 1797.
""",
    "max_new_tokens": 64,
    "temperature": 0.7,
    "do_sample": True,
    "stop_ids": [50278, 50279, 50277, 1, 0],
}
response = predictor_client.predict(
    data=data
)
print(response)

Below is an instruction that describes a task, paired with an input that provides further context. Write a response that appropriately completes the request.


When was George Washington president?

### Input:
George Washington (February 22, 1732[b] – December 14, 1799) was an American military officer, statesman,
and Founding Father who served as the first president of the United States from 1789 to 1797.



George Washington was the first president of the United States from 1789 to 1797.




## Delete Endpoint

In [ ]:
predictor.delete_model()
predictor.delete_endpoint()